Use this jupyterkernel:
``C:\Users\84551\AppData\Roaming\jupyter\kernels\engibench``

In [1]:
from engibench.problems.power_electronics import v0

# Create an empty problem
problem = v0.PowerElectronics()

init: power_electronics dir = d:\git_repos\EngiBench\engibench\problems\power_electronics
init... ngSpice64 dir = d:\git_repos\EngiBench\engibench\problems\power_electronics\ngSpice64\bin\ngspice.exe


In [2]:
original_netlist_path = "engibench/problems/power_electronics/data/netlist/5_4_3_6_10-dcdc_converter_1.net"  # sweep 141
bucket_id = "5_4_3_6_10"
problem.load_netlist(original_netlist_path, bucket_id)

In [ ]:
sweep_data = {
    "C_val": [0.000015485, 0.00001948, 0.000015185, 0.000002442, 0.000009287, 0.000015377],
    "L_val": [0.000354659, 0.000706596, 0.000195361],
    "T1_val": [0.867615857, 0.867615857, 0.867615857, 0.867615857, 0.867615857],
    "T2_val": [1, 1, 1, 1, 1],
    "L1_val": [1, 1, 0, 0, 1],
    "L2_val": [1, 1, 1, 0, 0],
}


sweep_data = {
    "C_val": [0.000015600, 0.00001948, 0.000015185, 0.000002442, 0.000009287, 0.000015377],
    "L_val": [0.000354659, 0.000706596, 0.000195361],
    "T1_val": [0.867615857, 0.867615857, 0.867615857, 0.867615857, 0.867615857],
    "T2_val": [1, 1, 1, 1, 1],
    "L1_val": [1, 0, 0, 1, 1],  # Another set that works: "L1_val": [1, 1, 0, 0, 1], "L2_val": [1, 1, 1, 0, 0]
    "L2_val": [1, 0, 1, 1, 0],
}

sweep_data = [
    0.000015600,
    0.00001948,
    0.000015185,
    0.000002442,
    0.000009287,
    0.000015377,  # C values
    0.000354659,
    0.000706596,
    0.000195361,  # L values
    0.867615857,  # T1
    1,
    0,
    0,
    1,
    1,  # GS_L1 values
    1,
    0,
    1,
    1,
    0,  # GS_L2 values
]

problem.simulate(design_variable=sweep_data)
print(problem.simulation_results)

rewriting netlist to: d:\git_repos\EngiBench\engibench\problems\power_electronics\data\netlist\rewrite_control_5_4_3_6_10-dcdc_converter_1.net
Running command: ['d:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\ngSpice64\\bin\\ngspice.exe', '-o', 'd:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\data\\log_file\\5_4_3_6_10-dcdc_converter_1.log', 'd:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\data\\netlist\\rewrite_control_5_4_3_6_10-dcdc_converter_1.net']
Error report from _calculate_efficiency: 8
[0.01244983 0.9094711  0.74045004]


To reproduce the previous bug caused by saving repeated `@R0[i]` and using `np.dtype()`:

In [ ]:
import numpy as np

names = ["time", "time", "time"]
formats = [np.float64] * 3
rowdtype = np.dtype({"names": names, "formats": formats})

ValueError: name already used as a name or title

Create sweep data matrix for dataset.

In [ ]:
# Range for C values: [1e-6, 2e-5]
# Range for L values: [1e-6, 1e-3]
# Range for T1 values: [0.1, 0.9]
# Keep the binary values the same for now.

import csv

import numpy as np

from engibench.problems.power_electronics import v0

# Create an empty problem
problem = v0.PowerElectronics()


original_netlist_path = "engibench/problems/power_electronics/data/netlist/5_4_3_6_10-dcdc_converter_1.net"  # sweep 141
bucket_id = "5_4_3_6_10"
problem.load_netlist(original_netlist_path, bucket_id)

sweep_data = [
    0.000015600,
    0.00001948,
    0.000015185,
    0.000002442,
    0.000009287,
    0.000015377,  # C values
    0.000354659,
    0.000706596,
    0.000195361,  # L values
    0.867615857,  # T1
    1,
    0,
    0,
    1,
    1,  # L1 values
    1,
    0,
    1,
    1,
    0,  # L2 values
]


def create_HF_dataset():
    n = 2  # number of iterpolation in each dimension

    count = 0
    count_stop = 10000000000000000000000
    with (
        open("./engibench/problems/power_electronics/data/dataset_V0_positive.csv", mode="w", newline="") as pos_file,
        open("./engibench/problems/power_electronics/data/dataset_V0_negative.csv", mode="w", newline="") as neg_file,
    ):
        """Python's csvmodule uses "\r\n"as the default newline character on platforms like Windows.
        When you're opening the file in text mode with the default line ending,
        the writer adds an extra line break."""

        header = "initial_design, DcGain, Voltage_Ripple\n"
        pos_file.write(header)
        neg_file.write(header)

        pos_writer = csv.writer(pos_file)
        neg_writer = csv.writer(neg_file)

        for C1 in np.linspace(1e-6, 2e-5, n):
            for C2 in np.linspace(1e-6, 2e-5, n):
                for C3 in np.linspace(1e-6, 2e-5, n):
                    for C4 in np.linspace(1e-6, 2e-5, n):
                        for C5 in np.linspace(1e-6, 2e-5, n):
                            for C6 in np.linspace(1e-6, 2e-5, n):
                                for L1 in np.linspace(1e-6, 1e-3, n):
                                    for L2 in np.linspace(1e-6, 1e-3, n):
                                        for L3 in np.linspace(1e-6, 1e-3, n):
                                            for T1 in np.linspace(0.1, 0.9, 9):  # this primarily affects g DcGain
                                                print("count", count, flush=True)
                                                count += 1
                                                sweep_data = [
                                                    C1,
                                                    C2,
                                                    C3,
                                                    C4,
                                                    C5,
                                                    C6,
                                                    L1,
                                                    L2,
                                                    L3,
                                                    T1,
                                                    1,
                                                    1,
                                                    0,
                                                    0,
                                                    1,  # GS#_L1 values
                                                    1,
                                                    1,
                                                    1,
                                                    0,
                                                    0,  # GS#_L2 values
                                                ]
                                                sweep_data = [
                                                    float(i) for i in sweep_data
                                                ]  # ensure all are floats, not np.float64
                                                problem.simulate(design_variable=sweep_data)
                                                g, r, e = problem.simulation_results
                                                g, r = np.abs(g), np.abs(r)

                                                if g is np.nan:
                                                    neg_writer.writerow([sweep_data, g, r])
                                                else:
                                                    pos_writer.writerow([sweep_data, g, r])

                                                if count >= count_stop:
                                                    return  # stop after count_stop iterations


create_HF_dataset()

init: power_electronics dir = d:\git_repos\EngiBench\engibench\problems\power_electronics
init... ngSpice64 dir = d:\git_repos\EngiBench\engibench\problems\power_electronics\ngSpice64\bin\ngspice.exe
count 0
rewriting netlist to: d:\git_repos\EngiBench\engibench\problems\power_electronics\data\netlist\rewrite_control_5_4_3_6_10-dcdc_converter_1.net
Running command: ['d:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\ngSpice64\\bin\\ngspice.exe', '-o', 'd:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\data\\log_file\\5_4_3_6_10-dcdc_converter_1.log', 'd:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\data\\netlist\\rewrite_control_5_4_3_6_10-dcdc_converter_1.net']
Error report from _calculate_efficiency: 8
count 1
rewriting netlist to: d:\git_repos\EngiBench\engibench\problems\power_electronics\data\netlist\rewrite_control_5_4_3_6_10-dcdc_converter_1.net
Running command: ['d:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\

In [ ]:
import numpy as np

from engibench.problems.power_electronics import v0

np.random.seed(23)

# Create an empty problem
problem = v0.PowerElectronics()


original_netlist_path = "engibench/problems/power_electronics/data/netlist/5_4_3_6_10-dcdc_converter_1.net"  # sweep 141
bucket_id = "5_4_3_6_10"
problem.load_netlist(original_netlist_path, bucket_id)


def create_HF_dataset_random():
    ranges = [
        [1e-6, 2e-5],
        [1e-6, 2e-5],
        [1e-6, 2e-5],
        [1e-6, 2e-5],
        [1e-6, 2e-5],
        [1e-6, 2e-5],
        [1e-6, 1e-3],
        [1e-6, 1e-3],
        [1e-6, 1e-3],
        [0.1, 0.9],
    ]

    N = 4608
    with (
        open(
            "./engibench/problems/power_electronics/data/dataset_V0_positive.csv", mode="a", newline=""
        ) as pos_file,  # append mode
        open("./engibench/problems/power_electronics/data/dataset_V0_negative.csv", mode="a", newline="") as neg_file,
    ):
        """Python's csvmodule uses "\r\n"as the default newline character on platforms like Windows.
        When you're opening the file in text mode with the default line ending,
        the writer adds an extra line break."""

        pos_writer = csv.writer(pos_file)
        neg_writer = csv.writer(neg_file)

        for i in range(N):
            sweep_data = [
                np.random.uniform(r[0] + 1e-9, r[1] - 1e-9) for r in ranges
            ]  # add an eps to avoid hitting the boundaries

            print("count", i, flush=True)
            sweep_data.extend(
                [
                    1,
                    1,
                    0,
                    0,
                    1,  # GS_L1 values
                    1,
                    1,
                    1,
                    0,
                    0,  # GS_L2 values)
                ]
            )
            sweep_data = [float(i) for i in sweep_data]  # ensure all are floats, not np.float64
            problem.simulate(design_variable=sweep_data)
            g, r, e = problem.simulation_results
            g, r = np.abs(g), np.abs(r)

            if g is np.nan:
                neg_writer.writerow([sweep_data, g, r])
                """ "[5.470606481885742e-06, 2.256069841740248e-06, 1.84220877224811e-05, 2.802574832344602e-06, 1.4090837528171452e-05, 1.5709161498656328e-05, 0.0003722193505794005, 8.356654381937486e-05, 0.000789321198521594, 0.12880487329723325,
                # 1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0]",
                # 0.6712372,0.007688817
                # If you want the list's numbers stored without quotes or brackets,
                # CSV format doesn't inherently support complex data types directly (lists).
                # In that case, you might need to consider alternative file formats like JSON or NumPy's .
                np.savez("data.npz", x=x, y=y, z=z)
x_loaded = data["x"]
y_loaded = data["y"]
z_loaded = data["z"]
np.pickle?
"""

            else:
                pos_writer.writerow([sweep_data, g, r])


create_HF_dataset_random()

init: power_electronics dir = d:\git_repos\EngiBench\engibench\problems\power_electronics
init... ngSpice64 dir = d:\git_repos\EngiBench\engibench\problems\power_electronics\ngSpice64\bin\ngspice.exe
count 0
rewriting netlist to: d:\git_repos\EngiBench\engibench\problems\power_electronics\data\netlist\rewrite_control_5_4_3_6_10-dcdc_converter_1.net
Running command: ['d:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\ngSpice64\\bin\\ngspice.exe', '-o', 'd:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\data\\log_file\\5_4_3_6_10-dcdc_converter_1.log', 'd:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\data\\netlist\\rewrite_control_5_4_3_6_10-dcdc_converter_1.net']
Error report from _calculate_efficiency: 8
count 1
rewriting netlist to: d:\git_repos\EngiBench\engibench\problems\power_electronics\data\netlist\rewrite_control_5_4_3_6_10-dcdc_converter_1.net
Running command: ['d:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\

In [ ]:
import numpy as np

from engibench.problems.power_electronics import v0

# Create an empty problem
problem = v0.PowerElectronics()


original_netlist_path = "engibench/problems/power_electronics/data/netlist/5_4_3_6_10-dcdc_converter_1.net"  # sweep 141
bucket_id = "5_4_3_6_10"
problem.load_netlist(original_netlist_path, bucket_id)


def latin_hypercube_sampling(N: int, ranges: list) -> np.ndarray:
    """Generate Latin Hypercube Samples in a high-dimensional space with custom ranges.

    :param N: Number of points to sample
    :param ranges: List of tuples [(min1, max1), (min2, max2), ...] defining the range for each dimension
    :return: LHS samples as a NumPy array of shape (N, len(ranges))
    """
    n_dim = len(ranges)
    intervals = np.linspace(0, 1, N + 1)[
        :-1
    ]  # Starting points of each interval: Create N+1 points and then exclude the last one.

    lhs = np.zeros((N, n_dim))
    for d in range(n_dim):
        # Shuffle intervals for each dimension
        permuted = np.random.permutation(N)
        lhs[:, d] = intervals[permuted] + np.random.uniform(
            1e-9, 1 / N, size=N
        )  # add an eps to avoid hitting the boundaries. np.random.uniform sample range is [low, high)

    # Scale each dimension to its respective range
    for d in range(n_dim):
        min_val, max_val = ranges[d]
        lhs[:, d] = min_val + (max_val - min_val) * lhs[:, d]

    return lhs


def create_HF_dataset_latin_hypercube():
    N = 4608  # Number of points to sample
    ranges = [
        [1e-6, 2e-5],
        [1e-6, 2e-5],
        [1e-6, 2e-5],
        [1e-6, 2e-5],
        [1e-6, 2e-5],
        [1e-6, 2e-5],
        [1e-6, 1e-3],
        [1e-6, 1e-3],
        [1e-6, 1e-3],
        [0.1, 0.9],
    ]  # Min and max for each dimension

    sweep_data_array = latin_hypercube_sampling(N, ranges)

    with (
        open(
            "./engibench/problems/power_electronics/data/dataset_V0_positive.csv", mode="a", newline=""
        ) as pos_file,  # append mode
        open("./engibench/problems/power_electronics/data/dataset_V0_negative.csv", mode="a", newline="") as neg_file,
    ):
        """Python's csvmodule uses "\r\n"as the default newline character on platforms like Windows.
        When you're opening the file in text mode with the default line ending,
        the writer adds an extra line break."""

        pos_writer = csv.writer(pos_file)
        neg_writer = csv.writer(neg_file)

        for i in range(N):
            print("count", i, flush=True)
            sweep_data = np.concatenate(
                (
                    sweep_data_array[i],
                    [
                        1,
                        1,
                        0,
                        0,
                        1,  # GS_L1 values
                        1,
                        1,
                        1,
                        0,
                        0,  # GS_L2 values)
                    ],
                )
            )
            sweep_data = [float(i) for i in sweep_data]  # ensure all are floats, not np.float64
            problem.simulate(design_variable=sweep_data)
            g, r, e = problem.simulation_results
            g, r = np.abs(g), np.abs(r)

            if g is np.nan:
                neg_writer.writerow([sweep_data, g, r])
            else:
                pos_writer.writerow([sweep_data, g, r])


create_HF_dataset_latin_hypercube()

count 0
rewriting netlist to: d:\git_repos\EngiBench\engibench\problems\power_electronics\data\netlist\rewrite_control_5_4_3_6_10-dcdc_converter_1.net
Running command: ['C:\\Program Files\\Spice64\\bin\\ngspice.exe', '-o', 'd:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\data\\log_file\\5_4_3_6_10-dcdc_converter_1.log', 'd:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\data\\netlist\\rewrite_control_5_4_3_6_10-dcdc_converter_1.net']
Error report from _calculate_efficiency: 8
count 1
rewriting netlist to: d:\git_repos\EngiBench\engibench\problems\power_electronics\data\netlist\rewrite_control_5_4_3_6_10-dcdc_converter_1.net
Running command: ['C:\\Program Files\\Spice64\\bin\\ngspice.exe', '-o', 'd:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\data\\log_file\\5_4_3_6_10-dcdc_converter_1.log', 'd:\\git_repos\\EngiBench\\engibench\\problems\\power_electronics\\data\\netlist\\rewrite_control_5_4_3_6_10-dcdc_converter_1.net']
Error report 

In [3]:
!python --version

Python 3.9.6


In [4]:
!huggingface-cli login

^C


In [16]:
def load_original_dataset():
    import ast
    import csv

    from datasets import Dataset

    # Open the CSV file for reading
    with open("./engibench/problems/power_electronics/data/dataset_V0_positive.csv") as pos_csv:
        reader = csv.reader(pos_csv)

        header = reader.__next__()
        print(header)
        # design, g, r = reader.__next__()
        # print(type(design), type(g), type(r))
        # print(ast.literal_eval(design))
        # print(float(g), float(r))

        dataset_list = []
        # Iterate over rows in the CSV file
        for design, g, r in reader:
            # convert the string representation of a list[float] into an actual Python list[float]
            dataset_list.append({header[0]: ast.literal_eval(design), header[1]: float(g), header[2]: float(r)})

    dataset_hf = Dataset.from_list(dataset_list)
    print(len(dataset_hf), dataset_hf[0])

    return dataset_hf


dataset_hf = load_original_dataset()
# dataset_hf.push_to_hub("IDEALLab/power_electronics_v0")  # No split yet. Default split is train.

['initial_design', ' DcGain', ' Voltage_Ripple']
13824 {'initial_design': [1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 0.1, 1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0], ' DcGain': 1.160767, ' Voltage_Ripple': 0.3441917}


Test if `Dataset.from_csv()` will work, specifically for the `initial_design`: string or list?

In [1]:
from datasets import Dataset

dataset = Dataset.from_csv("./engibench/problems/power_electronics/data/dataset_V0_positive.csv")

In [2]:
print(dataset[2])

{'initial_design': '[1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 0.30000000000000004, 1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0]', ' DcGain': 2.131255, ' Voltage_Ripple': 0.6461423}


Load from HF and split it into 7:2:1

In [6]:
from datasets import load_dataset

HF_dataset = load_dataset("IDEALLab/power_electronics_v0")
HF_dataset.keys()

dict_keys(['train'])

In [ ]:
print(HF_dataset["train"])  # need to specify "split"

Dataset({
    features: ['initial_design', ' DcGain', ' Voltage_Ripple'],
    num_rows: 13824
})


In [7]:
train_dataset = HF_dataset["train"]
len(train_dataset)

13824

In [8]:
train_dataset[0]

{'initial_design': [1e-06,
  1e-06,
  1e-06,
  1e-06,
  1e-06,
  1e-06,
  1e-06,
  1e-06,
  1e-06,
  0.1,
  1.0,
  1.0,
  0.0,
  0.0,
  1.0,
  1.0,
  1.0,
  1.0,
  0.0,
  0.0],
 ' DcGain': 1.160767,
 ' Voltage_Ripple': 0.3441917}

In [17]:
from datasets import DatasetDict
from datasets import load_dataset

# HF_dataset = load_dataset("IDEALLab/power_electronics_v0", split="train")
HF_dataset = load_original_dataset()
n = len(HF_dataset)
print(n)
split1 = int(n * 0.7)
split2 = int(n * 0.9)
train_ind = list(range(split1))
val_ind = list(range(split1, split2))
test_ind = list(range(split2, n))

shuffled_dataset = HF_dataset.shuffle(seed=523)

train_dataset = shuffled_dataset.select(train_ind)
print(train_dataset)

val_dataset = shuffled_dataset.select(val_ind)
test_dataset = shuffled_dataset.select(test_ind)

dataset_dict = DatasetDict({"train": train_dataset, "val": val_dataset, "test": test_dataset})
dataset_dict.push_to_hub("IDEALLab/power_electronics_v0")

['initial_design', ' DcGain', ' Voltage_Ripple']
13824 {'initial_design': [1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 1e-06, 0.1, 1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0], ' DcGain': 1.160767, ' Voltage_Ripple': 0.3441917}
13824
Dataset({
    features: ['initial_design', ' DcGain', ' Voltage_Ripple'],
    num_rows: 9676
})


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/3 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/575 [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/datasets/IDEALLab/power_electronics_v0/commit/29f81c5302bb9fdae17cdc3f5b7db9225fce9345', commit_message='Upload dataset', commit_description='', oid='29f81c5302bb9fdae17cdc3f5b7db9225fce9345', pr_url=None, repo_url=RepoUrl('https://huggingface.co/datasets/IDEALLab/power_electronics_v0', endpoint='https://huggingface.co', repo_type='dataset', repo_id='IDEALLab/power_electronics_v0'), pr_revision=None, pr_num=None)